In [13]:
'''

Analyze ingredient

'''

import nltk
#nltk.download()

from nltk.tokenize import word_tokenize

from nltk.chunk import ne_chunk

from nltk.tag import pos_tag

from nltk.tree import Tree

import pandas as pd

import os

In [14]:
# Try API

SampleTXT='The yellow dog barked at the cat'
SampleTXT='Korean cabbage; chicken breast; leeks; salt; sesame oil white sesame oil; white pepper; garlic; rice wine'.replace(';', '')

sentence= pos_tag(word_tokenize(SampleTXT))

print(sentence)


[('Korean', 'JJ'), ('cabbage', 'NN'), ('chicken', 'VBN'), ('breast', 'NN'), ('leeks', 'NN'), ('salt', 'NN'), ('sesame', 'JJ'), ('oil', 'NN'), ('white', 'JJ'), ('sesame', 'NN'), ('oil', 'NN'), ('white', 'JJ'), ('pepper', 'NN'), ('garlic', 'NN'), ('rice', 'NN'), ('wine', 'NN')]


In [15]:
for i in sentence:
    print(i[0], ' ', i[1])

Korean   JJ
cabbage   NN
chicken   VBN
breast   NN
leeks   NN
salt   NN
sesame   JJ
oil   NN
white   JJ
sesame   NN
oil   NN
white   JJ
pepper   NN
garlic   NN
rice   NN
wine   NN


In [16]:
grammar = "NP: {<DT>?<JJ>*<NN>}"

cp = nltk.RegexpParser(grammar)

result = cp.parse(sentence)

#print(result)

#result.draw()
for i, j in enumerate(result):
    print(i, j)

0 (NP Korean/JJ cabbage/NN)
1 ('chicken', 'VBN')
2 (NP breast/NN)
3 (NP leeks/NN)
4 (NP salt/NN)
5 (NP sesame/JJ oil/NN)
6 (NP white/JJ sesame/NN)
7 (NP oil/NN)
8 (NP white/JJ pepper/NN)
9 (NP garlic/NN)
10 (NP rice/NN)
11 (NP wine/NN)


In [17]:
# Try API
print(result)

(S
  (NP Korean/JJ cabbage/NN)
  chicken/VBN
  (NP breast/NN)
  (NP leeks/NN)
  (NP salt/NN)
  (NP sesame/JJ oil/NN)
  (NP white/JJ sesame/NN)
  (NP oil/NN)
  (NP white/JJ pepper/NN)
  (NP garlic/NN)
  (NP rice/NN)
  (NP wine/NN))


In [18]:
# Try API
print(result[0])
print('---')

for i in result[0]:
    print(i)
    
print('---')

for i in result[0][0]:
    print(i)

print('---')

print(result[0][0][0])
print(result[0][0][1])
result[0][0][1]

(NP Korean/JJ cabbage/NN)
---
('Korean', 'JJ')
('cabbage', 'NN')
---
Korean
JJ
---
Korean
JJ


'JJ'

In [19]:

'''
1. lower case
2. if there are [salt, soy sauce, egg, flour, butter, onion, shallot, chicken, beef, pork, fish, ] , replace the word to that
   else select Nouns [NN VBN]

'''
import ingredient_check_list
import ingredient_drop_list


# ex. Chicken breast
def analyze_word(tmpStr):
    checkList = ingredient_check_list.checkList
    dropList = ingredient_drop_list.dropList
    
    tmpStr = tmpStr.lower() # Chicken breast -> chicken breast
    
    if 'pig meat' in tmpStr and 'pig muscle' in tmpStr:
        return 'pork'
    
    for i in checkList:
        if i in tmpStr:
            return i
        
    if len(tmpStr.split(' ')) == 1:
        return tmpStr
    
    newStr = ''
    try:
        word_tokenized_list = pos_tag(word_tokenize(tmpStr)) # 'chicken breast' -> [('chicken', 'NN'), ('breast', 'NN')]
        for num_word_tokenized_list, i in enumerate(word_tokenized_list):
            if (i[1] == 'NN' or i[1] == 'VBN') and (len(i[0]) > 1): # Nouns and letter amount > 1
                check_drop = 0 # 1 -> drop, otherwise 0
                for drop_ingredient in dropList:
                    if i[0] == drop_ingredient:
                        check_drop = 1
                if check_drop == 0:
                    # if all condition above match -> add this ingredient
                    newStr += i[0]
                    if num_word_tokenized_list < len(word_tokenized_list) - 1:
                        newStr += ' '
        return newStr.strip()
    except:
        print('Unexpected Error!', tmpStr)
        return tmpStr.strip()
    
newStr = ''
for n, i in enumerate('Chicken breast; egg'.split(';')):
    newStr += analyze_word(i)
    if n < len('Chicken breast; egg'.split(';')) - 1:
        newStr += ';'
    print(analyze_word(i))
print('---')
print(newStr)
    

chicken
egg
---
chicken;egg


In [20]:
def list_to_string(tmpList, sep = ','):
    newStr = ''
    for n, i in enumerate(tmpList):
        newStr += i
        if n < len(tmpList) - 1:
            newStr += sep
    return newStr

In [21]:
import pandas as pd
import os

path = r'./res_chFormat'
if not os.path.isdir(path):
    os.mkdir(path)

df_origin = pd.read_csv(r'%s/iCook_ingredient_en.csv'%(path), engine='python', encoding='utf-8')
df = df_origin
df_origin

Cuisine  \
0                                    木耳炒雞片〞低醣低脂瘦身菜   
1                                      低卡《高麗菜雞肉水餃》   
2                                           毛豆仁煸雞丁   
3                                   減肥聖品：好嫩好多汁雞胸肉片   
4                                       減肥低脂-雞胸肉水餃   
5                                     蒜味鮮蔬煨大黃瓜一超簡單   
6                                             麻辣雞絲   
7                             泰式涼拌花枝涼拌透抽～低油低醣開胃涼拌菜   
8                                         低卡~秋葵雞胸卷   
9                                    [生酮低醣餐］檸檬起司蛋糕   
10                                     全麥蜂蜜司康＿無油高纖   
11                                          蝦仁豆腐蒸蛋   
12                                     【椰子芝麻脆餅】無奶油   
13                                泰式綠咖哩花椰菜濃湯＿低醣南洋味   
14                                         照燒豆腐漢堡排   
15                                           韓式海帶湯   
16                                        綠竹筍醬燒雞小腿   
17                                      骰子鯛魚豆腐【低醣】   
18                                        涼拌泰式蝦仁粉絲   
19                                         普羅旺斯燉蔬菜   
20                                     低碳水涼拌菜-雞絲白菜   
21                                           涼拌豆芽菜   
22                                [川味涼拌雞絲]雞胸肉不柴的撇步   
23                                     減脂便當菜🥗雙菇燴豆干   
24                                     減脂便當菜—雞肉豆腐排   
25                                  低卡青瓜雞柳蛋捲 （無澱粉）   
26                                       《鹹蛋山苦瓜雞絲》   
27                                  減肥好朋友《橄欖油嫩煎雞胸》   
28                                          《洋蔥炒肉》   
29                                          絲瓜燴金針菇   
...                                            ...   
28662                                    百香+芒果 冰淇淋   
28663                     「鷹牌煉奶‧煉上水果香濃滋味」芒果煉奶冰淇淋蛋糕   
28664                         (免冰淇淋機)香草奶油冰淇淋[邦妮廚房]   
28665                               粉紅自製蜂蜜冰淇淋(超簡單)   
28666                           123真簡單香草冰淇淋（免冰淇淋機）   
28667           冰淇淋DIY只要十分鐘（不需開火，不用冰箱版）【VICI的懶人廚房】   
28668                               5步香草冰淇淋(免冰淇淋機)   
28669               「COLD STONE-端午酷冰粽」中西MIX鐵觀音三角冰餅   
28670                                【肉桂打噴嚏】冰淇淋搓搓樂   
28671                                       地瓜乳酪布丁   
28672                      蜜桃冰淇淋 | Peach Ice Cream   
28673                               [踢那廚房] 盆栽冰淇淋蛋糕   
28674                                      芒果乳酪冰淇淋   
28675                                夏日必備~簡單清爽韓式泡菜   
28676                        【COLD STONE寶貝愛吃冰】南瓜甜心   
28677  [阿妮塔♥sweet] Mix&Fun黃金泡芙與COLD STONE冰淇淋的甜蜜派對。   
28678                                    牛奶冰淇淋餡 泡芙   
28679                                  桑椹草莓冰淇淋蜜糖金磚   
28680                                   南瓜子芝麻燕麥冰淇淋   
28681                                  不用烤〝檸檬冰舒芙蕾〞   
28682    藍莓起司蛋糕冰淇淋 Blueberry Cheesecake Ice cream    
28683              【大肚皮Jason主廚‧真男人廚房】初戀無限TOUCH檸檬布丁   
28684                               義式冰淇淋(香草牛奶吉拉朵)   
28685                               Bailey's 奶酒冰淇淋   
28686                               ㄚ曼達的廚房~冰淇淋馬芬蛋糕   
28687                               【烘焙零失敗】巧克力燕麥餅乾   
28688                          【吳双の愛妻甜點】低熱量的冰淇淋蘋果派   
28689                   Haagen Dazs冰淇淋自己在家做（免冰淇淋機）   
28690                   ♥開動 with Kat♥蜂蜜冰淇淋[不需冰淇淋機]   
28691              [SDS] 手工香草冰淇淋 Vanilla Ice Cream   

                                             Ingredients  \
0      Chicken breast; egg; black fungus; salt; water...   
1      Korean cabbage; chicken breast; leeks; salt; s...   
2      Chicken diced; cooked soybean kernel; pepper; ...   
3             Chicken breast; salt; pepper; dried chilli   
4      Chicken breast; onion, asparagus, cabbage vege...   
5      Large cucumber sliced; carrot slice; sliced ​​...   
6      Bone chicken breast; block; shallot; root; gin...   
7      Flowering circle circling; coriander; onion; l...   
8                             Chicken breast; salt; okra   
9      Gold flaxseed powder; iherb purchase; coconut ...   
10     Whole wheat flour; too whit

In [28]:

#practic
print(list(set(['apple', 'apple', 'bb', 'cc', 'aa', 'rr', 'bb'])))
print(list(set('flour;cream;flour;cream;sugar;water;bean;egg;egg'.split(';'))))
'chick' in 'chicken breast'
pos_tag(word_tokenize('chicken breast'))



['bb', 'cc', 'rr', 'aa', 'apple']
['cream', 'bean', 'flour', 'sugar', 'egg', 'water']


[('chicken', 'NN'), ('breast', 'NN')]

In [23]:
for num, rowData in enumerate(df['Ingredients']):
    print(num)
    print(rowData)
    newStr = ''
    for n, i in enumerate(rowData.split(';')):
        newStr += analyze_word(i)
        if (n < len(rowData.split(';')) - 1) and (analyze_word(i) != ''):
            newStr += ';'
        #print(analyze_word(i))
    print('---')
    print('>>', newStr)
    print('---\n')
    
    df['Ingredients'][num] = list_to_string(list(set(newStr.split(';'))), sep = ';')

0
Chicken breast; egg; black fungus; salt; water; white pepper
---
>> chicken;egg;fungus;salt;water;pepper
---

1
Korean cabbage; chicken breast; leeks; salt; sesame oil white sesame oil; white pepper; garlic; rice wine
---
>> cabbage;chicken;leeks;salt;oil;pepper;garlic;wine
---

2
Chicken diced; cooked soybean kernel; pepper; garlic; olive oil; salt; water; edible oil;
---
>> chicken;bean;pepper;garlic;oil;salt;water;oil;
---

3
Chicken breast; salt; pepper; dried chilli
---
>> chicken;salt;pepper;dried chilli
---

4
Chicken breast; onion, asparagus, cabbage vegetables; dumpling skin; rice wine; sesame oil; soy sauce; salt; black pepper;
---
>> chicken;onion;skin;wine;oil;soy sauce;salt;pepper;
---

5
Large cucumber sliced; carrot slice; sliced ​​mushroom; shallot segment; corn shoots half-cut; garlic; salt; edible oil;
---
>> cucumber;carrot slice;mushroom;shallot;corn;garlic;salt;oil;
---

6
Bone chicken breast; block; shallot; root; ginger; large slice; rice wine; soy cream; large

---
>> medium roll;egg;shallot;lemon juice
---

59
Potato; enoki mushroom; onion; soy sauce
---
>> potato;mushroom;onion;soy sauce
---

60
Pork ribs hot pot meat slice; carrot; oyster mushroom; shallot; salt; pepper
---
>> pork;carrot;mushroom;shallot;salt;pepper
---

61
Salmon fillet; lemon; soy sauce; pepper; onion; black pepper
---
>> fillet;lemon;soy sauce;pepper;onion;pepper
---

62
Chicken breast; low fat milk; broccoli; onion
---
>> chicken;milk;broccoli;onion
---

63
Pork meat; wet soy bean residue; salt bar; soy sauce; Shaoxing wine; ginger mud; white pepper powder;
---
>> pork;bean;salt;soy sauce;wine;ginger;pepper;
---

64
Boneless chicken leg; onion; flavor increase; soy sauce
---
>> chicken;onion;flavor increase;soy sauce
---

65
Korean cabbage; low-gluten flour; eggs; salt
---
>> cabbage;flour;egg;salt
---

66
Sweet potato; egg; onion; salt; pepper
---
>> sweet potato;egg;onion;salt;pepper
---

67
Chicken breast meat; home-made tofu; corn kernels; salt; black pepper
---
>

---
>> chicken;squid;salt;cabbage;mushroom;onion;garlic section;plum roll slice;shrimp;onion
---

123
Broad winter powder; onion; shiitake mushroom; carrot; white bamboo shoot; celery; cabbage; lean pork; 100g; onion; garlic; olive oil; 10g; cold water; shiitake mushroom; cold water; soaked winter powder; spicy bean paste; 15g; soy sauce; 45g
---
>> winter;onion;mushroom;carrot;bamboo shoot;celery;cabbage;pork;onion;garlic;oil;water;mushroom;water;soaked winter;bean;soy sauce;
---

124
Brown rice; millet; high-fiber vegetable and fruit chicken broth; chestnut; garlic; salt; white pepper; pig's hind leg lean diced;
---
>> rice;millet;chicken;chestnut;garlic;salt;pepper;pig hind leg lean;
---

125
Pleurotus eryngii; 蛤蛎; onion; bean sprouts; water; lemon; fish sauce; nine-story tower; ginger slices can be saved;
---
>> eryngii;蛤蛎;onion;bean;water;lemon;fish;tower;ginger;
---

126
Brown rice; millet; high-fiber vegetable and fruit chicken broth; sirloin diced; salt; white pepper; spinach c

>> pork;tofu;mushroom;cabbage;kimchi;garlic;shallot;noodle;chili sauce;wine;miso;
---

168
Egg; water; medium-gluten flour; corn flour; shallot; olive oil; salt; soy sauce;
---
>> egg;water;flour;flour;shallot;oil;salt;soy sauce;
---

169
Onion; savory hand; olive oil; white sesame; black fungus; carrot; cucumber; dried shiitake mushroom; winter powder; soy sauce; sesame oil; sugar;
---
>> onion;hand;oil;sesame;fungus;carrot;cucumber;mushroom;winter;soy sauce;oil;sugar;
---

170
Fan; egg; ham; gherkin; sesame oil; orange soy sauce
---
>> fan;egg;ham;gherkin;oil;soy sauce
---

171
Egg tofu; chestnut powder; oil; radish puree; soy sauce; taste Lin; water;
---
>> egg;chestnut;oil;puree;soy sauce;taste lin;water;
---

172
Japanese green crystal fans; carrot; ground meat; shiitake mushroom; bamboo shoots; ginger; onion; fungus; soy sauce; salt; Japanese white sesame oil; Japanese white pepper; Rizhengbao too white powder; eggs; salt; Flour
---
>> crystal;carrot;ground meat;mushroom;bamboo;g

>> muscle;tomato;onion;egg;oil;marinade;soy sauce;sugar;oil;water;
---

219
Mushroom; kelp; onion; onion; cabbage; chicken breast; salt; master of cooking; protein; celery
---
>> mushroom;kelp;onion;onion;cabbage;chicken;salt;master cooking;celery
---

220
Red bean paste; fine ground meat; beef head brand curry block; salted egg yolk; medium-gluten flour; cream; egg; sugar; milk powder; soy sauce; oil onion crisp; pepper; rice wine;
---
>> bean;ground meat;beef;egg;flour;cream;egg;sugar;milk;soy sauce;onion;pepper;wine;
---

221
Muscle in chicken; asparagus; mushroom; garlic; pepper; oil; salted chicken water; marinated chicken stuffed spicy bean paste; marinated chicken wine; salted chicken sauce; salted chicken meat too white; seasoning salt; seasoning pepper Seasoning sugar
---
>> chicken;asparagus;mushroom;garlic;pepper;oil;chicken;chicken;chicken;chicken;chicken;salt;pepper
---

222
Brown rice; preserved egg; three-color vegetables; eggs; vegetarian ham; onion; salt
---
>> rice;eg

...

---
>> beef;kiwi;garlic;onion;honey;soy sauce;teaspoon;oil;spoonful linseed;onion;sesame
---

28427
White rice; usually a cup of rice can be made in two rolls; sesame oil; salt; sesame; sushi with seaweed; egg; cut into 10 strips; cucumber; carrot; Japanese pickled yellow radish; cut 10 strips; Meat strips; Korean ham
---
>> rice;cup rice made;oil;salt;sesame;sushi seaweed;egg;cut;cucumber;carrot;radish;cut;meat;ham
---

28428
Korean winter powder; onion; combo savory hand; vegetable oil; white sesame; black fungus; carrot; cucumber; dried shiitake; soy sauce; Korean sesame oil; fructose;
---
>> winter;onion;savory hand;oil;sesame;fungus;carrot;cucumber;dried shiitake;soy sauce;oil;fructose;
---

28429
Wine; cuttlefish soaked; onion shredded spare; shallot cut spare; ginger shredded spare; good mushroom road snow white mushroom; good mushroom road Hongxi mushroom; sesame oil; cold boiled water; white vinegar; Korean chili sauce; soy sauce; sugar; Green onion and chopped; coriander and 

---
>> onion;lentil;cabbage;fungus;mushroom;soy sauce;sugar;water;pepper;rice cake;mushroom;carrot wire
---

28471
牛肉絲牛絞肉也OK;OR;豬絞肉不喜歡肉類的可不加;黃豆芽;紅蘿蔔;根;小黃瓜;蔥;小白菜;一小把;泡菜;0.5大匙;香油先炒香備用;蛋韓國香油普通香油也可以拉白芝麻;炒香過的;白飯;海苔絲;適量;拌飯醬汁;可用市售的拌飯醬或;韓式辣椒醬고추장混合均勻即成拌飯醬;醬油0.5大匙醋;1;小匙;糖;1小匙;蒜末;香油;1小匙;
---
>> 牛肉絲牛絞肉也ok;or;豬絞肉不喜歡肉類的可不加;黃豆芽;紅蘿蔔;根;小黃瓜;蔥;小白菜;一小把;泡菜;0.5大匙;香油先炒香備用;蛋韓國香油普通香油也可以拉白芝麻;炒香過的;白飯;海苔絲;適量;拌飯醬汁;可用市售的拌飯醬或;韓式辣椒醬고추장混合均勻即成拌飯醬;醬油0.5大匙醋;1;小匙;糖;1小匙;蒜末;香油;1小匙;
---

28472
Beef; green onion; green bean sprouts yellow bean sprouts; enoki mushroom; Korean winter powder; egg; onion; white radish; garlic; ginger; granule black pepper; green onion; water; chili powder; soy sauce; sesame oil; garlic; ginger; pepper;
---
>> beef;onion;bean;mushroom;winter;egg;onion;radish;garlic;ginger;pepper;onion;water;chili;soy sauce;oil;garlic;ginger;pepper;
---

28473
Medium-gluten flour; too white powder; onion; leeks; red radish; squash; sautéed; shrimp; scallops; eggs; water; oil; white sesame, chili powder; sauce; 3 ta

---
>> pork;onion;taste;material;oil;tune;taste;material;pepper;taste;material;salt;tune;taste;
---

28523
Boneless chicken leg ribs; onion; soy sauce; honey; Korean hot sauce; garlic
---
>> chicken;onion;soy sauce;honey;sauce;garlic
---

28524
Chicken breast; cheese slice; kimchi in Arirang village; bread flour; salt bar; pepper; salad oil; flour;
---
>> chicken;slice;village;flour;salt;pepper;oil;flour;
---

28525
One squid, tofu, Korean kimchi, green pepper, carrot, green onion, garlic. Korean hot sauce, salt, chicken powder, and white sugar.
---
>> onion
---

28526
Strip-shaped rice cake with half-cut; Korean cabbage; onion; carrot shred; shallot cut; Korean chili sauce; sugar; water;
---
>> rice cake half-cut;cabbage;onion;carrot;shallot;chili sauce;sugar;water;
---

28527
Protein; lemon juice; white sugar; egg yolk; Korean honey jujube sauce; water; low-gluten flour; corn flour
---
>> protein;lemon juice;sugar;egg;honey;water;flour;flour
---

28528
Egg; pepper; salt
---
>> egg;pe

---
>> rice cake;plum;sweet;onion;mushroom;spicy sauce;soy sauce;squid;water;
---

28571
Mountain bracken; onion silk; yellow bean sprouts; garlic; spicy oil; chili powder; ginger; beef high soup;
---
>> mountain bracken;onion;bean;garlic;oil;chili;ginger;beef;
---

28572
Winter powder; Korean rice cake; laurel fish dumpling; laurel egg dumpling; onion; kimchi; Korean spicy sauce; corn shoots; pig pork belly; sage; scorpion; enoki mushroom; tofu;
---
>> winter;rice cake;fish;egg;onion;spicy sauce;corn;pork;sage;scorpion;mushroom;tofu;
---

28573
Guiguan egg dumplings; laurel dumplings; garlic end; onion; sesame oil; Korean chili sauce; broth or water; apricot mushroom; corn shoots; taro stem; bean flower; beef slice; kimchi;
---
>> egg;laurel;end;onion;oil;chili sauce;water;mushroom;corn;taro stem;bean;beef;
---

28574
Laurel fish dumplings; laurel flower dumplings; laurel egg dumplings; tofu; meat slices; enoki mushroom; oyster mushroom; onion; kimchi; Korean chili sauce;
---
>> fish;

---
>> milk;cream;sugar;chocolate;cocoa;egg;maltose
---

28654
French bread; strips; eggs; one; milk; milliliters; cream; ice cream vanilla;
---
>> bread;egg;milk;cream;cream;
---

28655
Fresh milk; fresh cream; green tea powder; maltose; sugar; egg yolk
---
>> milk;cream;tea;maltose;sugar;egg
---

28656
Cocoa hurricane cake; sheet mousse cream cheese cream; cheese; mousse body sugar; mousse body gelatin; mousse body orange wine Grand; Marnier; mousse body egg yolk; mousse body orange juice; mousse Body animal fresh cream; mousse body water; jelly blueberry juice; jelly water; jelly sugar; jelly Geely T; blueberry
---
>> cocoa;cream;cheese;sugar;mousse body gelatin;wine;marnier;egg;mousse body orange juice;cream;water;juice;water;sugar;blueberry
---

28657
鬆餅粉;蛋;楓糖漿;香草冰淇淋;巧克力醬;香蕉;鮮奶油
---
>> 鬆餅粉;蛋;楓糖漿;香草冰淇淋;巧克力醬;香蕉;鮮奶油
---

28658
Vanilla pods; fresh milk; fresh cream; egg yolk; fine sugar; ice cubes;
---
>> vanilla;milk;cream;egg;sugar;ice;
---

28659
Unsalted cream; fresh milk; egg; fi

In [24]:
df

Cuisine  \
0                                    木耳炒雞片〞低醣低脂瘦身菜   
1                                      低卡《高麗菜雞肉水餃》   
2                                           毛豆仁煸雞丁   
3                                   減肥聖品：好嫩好多汁雞胸肉片   
4                                       減肥低脂-雞胸肉水餃   
5                                     蒜味鮮蔬煨大黃瓜一超簡單   
6                                             麻辣雞絲   
7                             泰式涼拌花枝涼拌透抽～低油低醣開胃涼拌菜   
8                                         低卡~秋葵雞胸卷   
9                                    [生酮低醣餐］檸檬起司蛋糕   
10                                     全麥蜂蜜司康＿無油高纖   
11                                          蝦仁豆腐蒸蛋   
12                                     【椰子芝麻脆餅】無奶油   
13                                泰式綠咖哩花椰菜濃湯＿低醣南洋味   
14                                         照燒豆腐漢堡排   
15                                           韓式海帶湯   
16                                        綠竹筍醬燒雞小腿   
17                                      骰子鯛魚豆腐【低醣】   
18                                        涼拌泰式蝦仁粉絲   
19                                         普羅旺斯燉蔬菜   
20                                     低碳水涼拌菜-雞絲白菜   
21                                           涼拌豆芽菜   
22                                [川味涼拌雞絲]雞胸肉不柴的撇步   
23                                     減脂便當菜🥗雙菇燴豆干   
24                                     減脂便當菜—雞肉豆腐排   
25                                  低卡青瓜雞柳蛋捲 （無澱粉）   
26                                       《鹹蛋山苦瓜雞絲》   
27                                  減肥好朋友《橄欖油嫩煎雞胸》   
28                                          《洋蔥炒肉》   
29                                          絲瓜燴金針菇   
...                                            ...   
28662                                    百香+芒果 冰淇淋   
28663                     「鷹牌煉奶‧煉上水果香濃滋味」芒果煉奶冰淇淋蛋糕   
28664                         (免冰淇淋機)香草奶油冰淇淋[邦妮廚房]   
28665                               粉紅自製蜂蜜冰淇淋(超簡單)   
28666                           123真簡單香草冰淇淋（免冰淇淋機）   
28667           冰淇淋DIY只要十分鐘（不需開火，不用冰箱版）【VICI的懶人廚房】   
28668                               5步香草冰淇淋(免冰淇淋機)   
28669               「COLD STONE-端午酷冰粽」中西MIX鐵觀音三角冰餅   
28670                                【肉桂打噴嚏】冰淇淋搓搓樂   
28671                                       地瓜乳酪布丁   
28672                      蜜桃冰淇淋 | Peach Ice Cream   
28673                               [踢那廚房] 盆栽冰淇淋蛋糕   
28674                                      芒果乳酪冰淇淋   
28675                                夏日必備~簡單清爽韓式泡菜   
28676                        【COLD STONE寶貝愛吃冰】南瓜甜心   
28677  [阿妮塔♥sweet] Mix&Fun黃金泡芙與COLD STONE冰淇淋的甜蜜派對。   
28678                                    牛奶冰淇淋餡 泡芙   
28679                                  桑椹草莓冰淇淋蜜糖金磚   
28680                                   南瓜子芝麻燕麥冰淇淋   
28681                                  不用烤〝檸檬冰舒芙蕾〞   
28682    藍莓起司蛋糕冰淇淋 Blueberry Cheesecake Ice cream    
28683              【大肚皮Jason主廚‧真男人廚房】初戀無限TOUCH檸檬布丁   
28684                               義式冰淇淋(香草牛奶吉拉朵)   
28685                               Bailey's 奶酒冰淇淋   
28686                               ㄚ曼達的廚房~冰淇淋馬芬蛋糕   
28687                               【烘焙零失敗】巧克力燕麥餅乾   
28688                          【吳双の愛妻甜點】低熱量的冰淇淋蘋果派   
28689                   Haagen Dazs冰淇淋自己在家做（免冰淇淋機）   
28690                   ♥開動 with Kat♥蜂蜜冰淇淋[不需冰淇淋機]   
28691              [SDS] 手工香草冰淇淋 Vanilla Ice Cream   

                                             Ingredients  \
0                   fungus;salt;pepper;chicken;egg;water   
1      cabbage;garlic;leeks;oil;salt;wine;chicken;pepper   
2             ;garlic;oil;salt;bean;water;chicken;pepper   
3                       dried chilli;salt;chicken;pepper   
4      ;onion;oil;salt;skin;wine;chicken;soy sauce;pe...   
5      ;cucumber;garlic;oil;salt;corn;shallot;mushroo...   
6      ;cream;oil;bit;point;shallot;root;spoon;vinega...   
7      ;chili sauce;onion;coriander;fish;juice flower...   
8                                      okra;salt;chicken   
9      purchase;cream;juice;gelatin;vanilla;flour;coc...   
10                      ;milk;salt

In [ ]:
len('a')

In [ ]:
pd.DataFrame([['aa', 'aa', 'bb', 'cc', 'aa', 'rr', 'bb']])